In [1]:
import pandas as pd


In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import os
import keras
# from keras.models import Sequential
# from keras.layers import Flatten, Dense, Lambda
# from keras.layers import Convolution2D
# from keras.layers.pooling import MaxPooling2D
# from keras.layers import Cropping2D
# from keras.layers.core import Dense, Dropout, Activation
# from keras.layers import Dense, Conv1D, Flatten, MaxPooling1D
# from keras import regularizers
# from keras.layers import BatchNormalization
# from keras.utils import np_utils
# from keras.utils import plot_model
import graphviz, pydot, pydotplus
from sklearn.model_selection import train_test_split
# import tensorflow as tf

In [3]:
root_folder = "h"
healthy = []
for root, dirs, files in os.walk(root_folder):  
    for filename in files:
        healthy.append(filename)
print(healthy)

['image_cortex_patient15012020_633nm_obj20_power100_1sec_acc1_сenter2900 (2).txt', 'image_cortex_patient20022019_633nm_obj20_power100_1sec_сenter2900 (1).txt', 'image_cortex_patient15012020_633nm_obj20_power100_1sec_acc1_сenter2900 (1).txt', 'image_cortex_patient20022019_633nm_obj20_power100_1sec_сenter2900.txt', 'image_cortex_patient13012020_633nm_obj20_power100_1sec_step4um_сenter2900.txt', 'image_cortex_patient25022020_633nm_obj20_power100_1sec_сenter2900.txt', 'image_cortex_patient15012020_633nm_obj20_power100_2sec_acc1_сenter2900.txt', 'image_cortex_patient78_633nm_obj20_power100_step4um_2sec_acc1_сenter2900.txt', 'image_cortex_patient25022020_633nm_obj20_power100_2sec_сenter2900.txt', 'image_cortex_patient15012020_633nm_obj20_power100_1sec_acc1_сenter2900.txt']


In [4]:
measurements = []
classifications = []
points = []

In [5]:
count_healthy = 0

for name in healthy:
    df = pd.read_csv("h/" + name, sep='\t',skiprows=[0],
                     header=None, names=['X', 'Y', 'Wave', 'Intensity'])
    for i in range(len(df)//1015):
        measurements.append(df[['Intensity']][i*1015:(i+1)*1015].to_numpy())
        classifications.append([1,0])
        points.append(df[["X", "Y"]].iloc[i * 1015].values)
        count_healthy += 1

In [6]:
root_folder = "s/"
sick = []
for root, dirs, files in os.walk(root_folder):  
    for filename in files:
        sick.append(filename)

In [7]:
count_sick = 0

for name in sick:
    df = pd.read_csv("s/" + name, sep='\t',skiprows=[0],
                     header=None, names=['X', 'Y', 'Wave', 'Intensity'])
    for i in range(len(df)//1015):
        measurements.append(df[['Intensity']][i*1015:(i+1)*1015].to_numpy())
        classifications.append([0,1])
        count_sick += 1

In [8]:
X = np.asarray(measurements)
y = np.asarray(classifications)

In [9]:
X.shape

(6348, 1015, 1)

In [10]:
X = X.reshape(-1, 1015)
X.shape

(6348, 1015)

In [11]:
y.shape

(6348, 2)

In [12]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42)
print(f'Total amount of train measurements: {X_train.shape}')
print(f'Total amount of train labels: {y_train.shape}')
print(f'Total amount of test measurements: {X_test.shape}')
print(f'Total amount of test labels: {y_test.shape}')
y_train_labels = np.argmax(y_train, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

Total amount of train measurements: (4761, 1015)
Total amount of train labels: (4761, 2)
Total amount of test measurements: (1587, 1015)
Total amount of test labels: (1587, 2)


In [13]:
#from scipy.signal import savgol_filter
#for i in range(len(X_train)):
 #   X_train[i] = savgol_filter(X_train[i], 101, 2)
#for i in range(len(X_test)):
 #   X_test[i] = savgol_filter(X_test[i], 101, 2)

In [14]:
from catboost import CatBoostClassifier
from sklearn.metrics import f1_score, accuracy_score
from optuna.samplers import TPESampler
def objective(trial):
    param = {
        "iterations": trial.suggest_int("iterations", 100, 2000, step=100),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 1),
        "l2_leaf_reg": trial.suggest_int("l2_leaf_reg", 1e-7, 100.0),
        "border_count": trial.suggest_int("border_count", 1, 200, step=10),
        "random_strength": trial.suggest_float("random_strength", 1e-8, 10.0),
        "max_ctr_complexity": trial.suggest_int("max_ctr_complexity", 1, 5),
        "objective": trial.suggest_categorical("objective", ["Logloss", "MultiClassOneVsAll"]),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1),
        "depth": trial.suggest_int("depth", 3, 12),
        "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
        "bootstrap_type": trial.suggest_categorical(
            "bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]
        ),
        "od_type": trial.suggest_categorical("od_type", ["IncToDec", "Iter"]),
        "od_wait": trial.suggest_int("od_wait", 1, 50),
    }
    if param["bootstrap_type"] == "Bayesian":
        param["bagging_temperature"] = trial.suggest_float("bagging_temperature", 0, 10)
    elif param["bootstrap_type"] == "Bernoulli":
        param["subsample"] = trial.suggest_float("subsample", 0.1, 1)

    cat_cls = CatBoostClassifier(**param)

    cat_cls.fit(X_train, y_train_labels, verbose=1)

    preds = cat_cls.predict(X_test)
    f1 = f1_score(y_test_labels, cat_cls.predict(X_test))
    return f1

/opt/homebrew/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [15]:
import optuna

sampler = TPESampler(seed=1)
study = optuna.create_study(study_name="catboost", direction="maximize", sampler=sampler)
study.optimize(objective, n_trials=100000)

[I 2023-05-14 21:04:05,614] A new study created in memory with name: catboost
/opt/homebrew/lib/python3.10/site-packages/optuna/distributions.py:716: UserWarning: The distribution is specified by [1, 200] and step=10, but the range is not divisible by `step`. It will be replaced by [1, 191].
  warnings.warn(


0:	learn: 0.5405981	total: 65.2ms	remaining: 58.6s
1:	learn: 0.4952750	total: 73.7ms	remaining: 33.1s
2:	learn: 0.4763495	total: 80.9ms	remaining: 24.2s
3:	learn: 0.4618527	total: 90.8ms	remaining: 20.3s
4:	learn: 0.4511145	total: 97.6ms	remaining: 17.5s
5:	learn: 0.4430600	total: 107ms	remaining: 15.9s
6:	learn: 0.4356038	total: 116ms	remaining: 14.7s
7:	learn: 0.4319600	total: 122ms	remaining: 13.6s
8:	learn: 0.4274220	total: 129ms	remaining: 12.7s
9:	learn: 0.4234061	total: 136ms	remaining: 12.1s
10:	learn: 0.4200997	total: 146ms	remaining: 11.8s
11:	learn: 0.4166435	total: 153ms	remaining: 11.3s
12:	learn: 0.4122686	total: 160ms	remaining: 10.9s
13:	learn: 0.4077553	total: 165ms	remaining: 10.5s
14:	learn: 0.4021962	total: 174ms	remaining: 10.3s
15:	learn: 0.3970733	total: 181ms	remaining: 10s
16:	learn: 0.3886758	total: 188ms	remaining: 9.75s
17:	learn: 0.3853384	total: 197ms	remaining: 9.64s
18:	learn: 0.3805433	total: 203ms	remaining: 9.42s
19:	learn: 0.3739574	total: 210ms	rema

182:	learn: 0.0857059	total: 1.49s	remaining: 5.84s
183:	learn: 0.0851414	total: 1.5s	remaining: 5.83s
184:	learn: 0.0846846	total: 1.5s	remaining: 5.81s
185:	learn: 0.0839102	total: 1.51s	remaining: 5.81s
186:	learn: 0.0837031	total: 1.52s	remaining: 5.79s
187:	learn: 0.0828970	total: 1.53s	remaining: 5.78s
188:	learn: 0.0826924	total: 1.53s	remaining: 5.77s
189:	learn: 0.0825578	total: 1.54s	remaining: 5.76s
190:	learn: 0.0823680	total: 1.55s	remaining: 5.75s
191:	learn: 0.0819960	total: 1.56s	remaining: 5.74s
192:	learn: 0.0817138	total: 1.56s	remaining: 5.73s
193:	learn: 0.0810988	total: 1.57s	remaining: 5.72s
194:	learn: 0.0807619	total: 1.58s	remaining: 5.71s
195:	learn: 0.0802991	total: 1.59s	remaining: 5.7s
196:	learn: 0.0800388	total: 1.59s	remaining: 5.69s
197:	learn: 0.0796458	total: 1.6s	remaining: 5.68s
198:	learn: 0.0789040	total: 1.61s	remaining: 5.67s
199:	learn: 0.0778457	total: 1.62s	remaining: 5.66s
200:	learn: 0.0767125	total: 1.63s	remaining: 5.66s
201:	learn: 0.07

365:	learn: 0.0340689	total: 2.92s	remaining: 4.26s
366:	learn: 0.0340194	total: 2.93s	remaining: 4.25s
367:	learn: 0.0340050	total: 2.94s	remaining: 4.25s
368:	learn: 0.0338531	total: 2.94s	remaining: 4.24s
369:	learn: 0.0337781	total: 2.95s	remaining: 4.23s
370:	learn: 0.0336118	total: 2.96s	remaining: 4.22s
371:	learn: 0.0335156	total: 2.97s	remaining: 4.21s
372:	learn: 0.0332135	total: 2.98s	remaining: 4.2s
373:	learn: 0.0331104	total: 2.98s	remaining: 4.19s
374:	learn: 0.0331008	total: 2.99s	remaining: 4.18s
375:	learn: 0.0329515	total: 3s	remaining: 4.18s
376:	learn: 0.0327516	total: 3.01s	remaining: 4.17s
377:	learn: 0.0324151	total: 3.02s	remaining: 4.16s
378:	learn: 0.0322380	total: 3.02s	remaining: 4.16s
379:	learn: 0.0320525	total: 3.03s	remaining: 4.15s
380:	learn: 0.0319861	total: 3.04s	remaining: 4.14s
381:	learn: 0.0319783	total: 3.04s	remaining: 4.13s
382:	learn: 0.0318519	total: 3.05s	remaining: 4.12s
383:	learn: 0.0315905	total: 3.06s	remaining: 4.11s
384:	learn: 0.03

549:	learn: 0.0192386	total: 4.34s	remaining: 2.76s
550:	learn: 0.0192044	total: 4.34s	remaining: 2.75s
551:	learn: 0.0191619	total: 4.35s	remaining: 2.74s
552:	learn: 0.0191480	total: 4.36s	remaining: 2.74s
553:	learn: 0.0191181	total: 4.37s	remaining: 2.73s
554:	learn: 0.0189876	total: 4.38s	remaining: 2.72s
555:	learn: 0.0189871	total: 4.38s	remaining: 2.71s
556:	learn: 0.0189855	total: 4.39s	remaining: 2.7s
557:	learn: 0.0189132	total: 4.4s	remaining: 2.69s
558:	learn: 0.0188834	total: 4.4s	remaining: 2.69s
559:	learn: 0.0187858	total: 4.42s	remaining: 2.68s
560:	learn: 0.0187693	total: 4.42s	remaining: 2.67s
561:	learn: 0.0187101	total: 4.43s	remaining: 2.66s
562:	learn: 0.0186921	total: 4.44s	remaining: 2.65s
563:	learn: 0.0186898	total: 4.45s	remaining: 2.65s
564:	learn: 0.0186604	total: 4.45s	remaining: 2.64s
565:	learn: 0.0186364	total: 4.46s	remaining: 2.63s
566:	learn: 0.0186085	total: 4.47s	remaining: 2.62s
567:	learn: 0.0184289	total: 4.48s	remaining: 2.62s
568:	learn: 0.0

...

1817:	learn: 0.0294158	total: 12m 50s	remaining: 34.8s
1818:	learn: 0.0294046	total: 12m 50s	remaining: 34.3s
1819:	learn: 0.0293963	total: 12m 51s	remaining: 33.9s
1820:	learn: 0.0293875	total: 12m 51s	remaining: 33.5s
1821:	learn: 0.0293584	total: 12m 52s	remaining: 33.1s
1822:	learn: 0.0293313	total: 12m 52s	remaining: 32.6s
1823:	learn: 0.0293254	total: 12m 53s	remaining: 32.2s
1824:	learn: 0.0293089	total: 12m 53s	remaining: 31.8s
1825:	learn: 0.0292971	total: 12m 53s	remaining: 31.4s
1826:	learn: 0.0292793	total: 12m 54s	remaining: 30.9s
1827:	learn: 0.0292710	total: 12m 54s	remaining: 30.5s
1828:	learn: 0.0292511	total: 12m 55s	remaining: 30.1s
1829:	learn: 0.0292353	total: 12m 55s	remaining: 29.7s
1830:	learn: 0.0292254	total: 12m 56s	remaining: 29.2s
1831:	learn: 0.0292079	total: 12m 56s	remaining: 28.8s
1832:	learn: 0.0291968	total: 12m 56s	remaining: 28.4s
1833:	learn: 0.0291868	total: 12m 57s	remaining: 28s
1834:	learn: 0.0291740	total: 12m 57s	remaining: 27.5s
1835:	learn:

[I 2023-05-14 23:39:09,770] Trial 62 finished with value: 0.8716157205240175 and parameters: {'iterations': 1900, 'learning_rate': 0.9602444257610754, 'l2_leaf_reg': 17, 'border_count': 61, 'random_strength': 4.758094067654059, 'max_ctr_complexity': 2, 'objective': 'MultiClassOneVsAll', 'colsample_bylevel': 0.0914913782264765, 'depth': 11, 'boosting_type': 'Ordered', 'bootstrap_type': 'MVS', 'od_type': 'IncToDec', 'od_wait': 4}. Best is trial 42 with value: 0.8842471714534378.
/opt/homebrew/lib/python3.10/site-packages/optuna/distributions.py:716: UserWarning: The distribution is specified by [1, 200] and step=10, but the range is not divisible by `step`. It will be replaced by [1, 191].
  warnings.warn(


0:	learn: 0.6187008	total: 12.8s	remaining: 7h 7m 28s
1:	learn: 0.6025374	total: 27.4s	remaining: 7h 35m 42s
2:	learn: 0.5961645	total: 39.3s	remaining: 7h 16m 24s
3:	learn: 0.5908286	total: 53.8s	remaining: 7h 27m 19s
4:	learn: 0.5891071	total: 1m 6s	remaining: 7h 22m 56s
5:	learn: 0.5852042	total: 1m 18s	remaining: 7h 17m 28s
6:	learn: 0.5835476	total: 1m 31s	remaining: 7h 15m 40s
7:	learn: 0.5819110	total: 1m 43s	remaining: 7h 11m 24s
8:	learn: 0.5806307	total: 1m 56s	remaining: 7h 9m 15s
9:	learn: 0.5796034	total: 2m 8s	remaining: 7h 5m 33s
10:	learn: 0.5788773	total: 2m 19s	remaining: 7h 39s
11:	learn: 0.5774223	total: 2m 31s	remaining: 6h 58m 45s
12:	learn: 0.5763065	total: 2m 46s	remaining: 7h 3m 28s
13:	learn: 0.5749038	total: 2m 59s	remaining: 7h 3m 14s
14:	learn: 0.5728170	total: 3m 12s	remaining: 7h 3m 48s


[W 2023-05-14 23:42:36,800] Trial 63 failed with parameters: {'iterations': 2000, 'learning_rate': 0.8551693516459535, 'l2_leaf_reg': 3, 'border_count': 1, 'random_strength': 3.869906101693599, 'max_ctr_complexity': 2, 'objective': 'MultiClassOneVsAll', 'colsample_bylevel': 0.09710641978285788, 'depth': 12, 'boosting_type': 'Ordered', 'bootstrap_type': 'MVS', 'od_type': 'IncToDec', 'od_wait': 11} because of the following error: KeyboardInterrupt('').
Traceback (most recent call last):
  File "/opt/homebrew/lib/python3.10/site-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(trial)
  File "/var/folders/ym/m5symfp11nzfwgr30yqmsw3xtkhq7t/T/ipykernel_56558/1092283874.py", line 29, in objective
    cat_cls.fit(X_train, y_train_labels, verbose=1)
  File "/opt/homebrew/lib/python3.10/site-packages/catboost/core.py", line 5131, in fit
    self._fit(X, y, cat_features, text_features, embedding_features, None, sample_weight, None, None, None, None, baseline

KeyboardInterrupt: 

In [18]:

cat_cls = CatBoostClassifier(**study.best_params)

cat_cls.fit(X_train, y_train_labels, verbose=1)

preds = cat_cls.predict(X_test)
f1 = f1_score(y_test_labels, cat_cls.predict(X_test))

0:	learn: 0.5626694	total: 122ms	remaining: 3m 51s
1:	learn: 0.5089519	total: 252ms	remaining: 3m 59s
2:	learn: 0.4839132	total: 411ms	remaining: 4m 20s
3:	learn: 0.4665915	total: 550ms	remaining: 4m 20s
4:	learn: 0.4535126	total: 703ms	remaining: 4m 26s
5:	learn: 0.4443341	total: 850ms	remaining: 4m 28s
6:	learn: 0.4374298	total: 1.01s	remaining: 4m 33s
7:	learn: 0.4345404	total: 1.16s	remaining: 4m 35s
8:	learn: 0.4307731	total: 1.29s	remaining: 4m 31s
9:	learn: 0.4254447	total: 1.42s	remaining: 4m 29s
10:	learn: 0.4211023	total: 1.59s	remaining: 4m 32s
11:	learn: 0.4180448	total: 1.71s	remaining: 4m 28s
12:	learn: 0.4149827	total: 1.88s	remaining: 4m 33s
13:	learn: 0.4102138	total: 2.03s	remaining: 4m 33s
14:	learn: 0.4057955	total: 2.14s	remaining: 4m 28s
15:	learn: 0.3981757	total: 2.3s	remaining: 4m 30s
16:	learn: 0.3919326	total: 2.47s	remaining: 4m 33s
17:	learn: 0.3840155	total: 2.61s	remaining: 4m 32s
18:	learn: 0.3802974	total: 2.74s	remaining: 4m 30s
19:	learn: 0.3736255	to

158:	learn: 0.1544502	total: 24.1s	remaining: 4m 24s
159:	learn: 0.1535264	total: 24.3s	remaining: 4m 23s
160:	learn: 0.1530980	total: 24.4s	remaining: 4m 23s
161:	learn: 0.1524123	total: 24.5s	remaining: 4m 23s
162:	learn: 0.1515036	total: 24.7s	remaining: 4m 23s
163:	learn: 0.1512018	total: 24.8s	remaining: 4m 22s
164:	learn: 0.1506496	total: 25s	remaining: 4m 23s
165:	learn: 0.1501142	total: 25.2s	remaining: 4m 22s
166:	learn: 0.1491806	total: 25.3s	remaining: 4m 22s
167:	learn: 0.1486650	total: 25.4s	remaining: 4m 22s
168:	learn: 0.1478911	total: 25.6s	remaining: 4m 21s
169:	learn: 0.1475198	total: 25.7s	remaining: 4m 21s
170:	learn: 0.1472848	total: 25.9s	remaining: 4m 21s
171:	learn: 0.1468627	total: 26s	remaining: 4m 21s
172:	learn: 0.1461718	total: 26.2s	remaining: 4m 21s
173:	learn: 0.1457329	total: 26.3s	remaining: 4m 20s
174:	learn: 0.1455150	total: 26.4s	remaining: 4m 20s
175:	learn: 0.1452748	total: 26.6s	remaining: 4m 20s
176:	learn: 0.1446080	total: 26.8s	remaining: 4m 2

315:	learn: 0.0891199	total: 47.7s	remaining: 3m 59s
316:	learn: 0.0890369	total: 47.9s	remaining: 3m 59s
317:	learn: 0.0887905	total: 48s	remaining: 3m 58s
318:	learn: 0.0886808	total: 48.2s	remaining: 3m 58s
319:	learn: 0.0885424	total: 48.4s	remaining: 3m 58s
320:	learn: 0.0883595	total: 48.5s	remaining: 3m 58s
321:	learn: 0.0881861	total: 48.6s	remaining: 3m 58s
322:	learn: 0.0880239	total: 48.7s	remaining: 3m 58s
323:	learn: 0.0878654	total: 48.9s	remaining: 3m 57s
324:	learn: 0.0874496	total: 49s	remaining: 3m 57s
325:	learn: 0.0872901	total: 49.2s	remaining: 3m 57s
326:	learn: 0.0870356	total: 49.3s	remaining: 3m 57s
327:	learn: 0.0868561	total: 49.4s	remaining: 3m 56s
328:	learn: 0.0865922	total: 49.6s	remaining: 3m 56s
329:	learn: 0.0863912	total: 49.7s	remaining: 3m 56s
330:	learn: 0.0860990	total: 49.8s	remaining: 3m 56s
331:	learn: 0.0860039	total: 50s	remaining: 3m 56s
332:	learn: 0.0857060	total: 50.2s	remaining: 3m 56s
333:	learn: 0.0853980	total: 50.4s	remaining: 3m 56s

472:	learn: 0.0619067	total: 1m 10s	remaining: 3m 33s
473:	learn: 0.0618690	total: 1m 10s	remaining: 3m 33s
474:	learn: 0.0617475	total: 1m 10s	remaining: 3m 32s
475:	learn: 0.0616627	total: 1m 11s	remaining: 3m 32s
476:	learn: 0.0615460	total: 1m 11s	remaining: 3m 32s
477:	learn: 0.0614140	total: 1m 11s	remaining: 3m 32s
478:	learn: 0.0612398	total: 1m 11s	remaining: 3m 32s
479:	learn: 0.0611705	total: 1m 11s	remaining: 3m 32s
480:	learn: 0.0610416	total: 1m 11s	remaining: 3m 32s
481:	learn: 0.0609427	total: 1m 12s	remaining: 3m 31s
482:	learn: 0.0607923	total: 1m 12s	remaining: 3m 31s
483:	learn: 0.0606971	total: 1m 12s	remaining: 3m 31s
484:	learn: 0.0605280	total: 1m 12s	remaining: 3m 31s
485:	learn: 0.0604478	total: 1m 12s	remaining: 3m 31s
486:	learn: 0.0603475	total: 1m 12s	remaining: 3m 31s
487:	learn: 0.0602757	total: 1m 12s	remaining: 3m 30s
488:	learn: 0.0601012	total: 1m 13s	remaining: 3m 30s
489:	learn: 0.0599287	total: 1m 13s	remaining: 3m 30s
490:	learn: 0.0598547	total:

625:	learn: 0.0473739	total: 1m 33s	remaining: 3m 10s
626:	learn: 0.0473299	total: 1m 33s	remaining: 3m 10s
627:	learn: 0.0472732	total: 1m 33s	remaining: 3m 10s
628:	learn: 0.0472191	total: 1m 33s	remaining: 3m 9s
629:	learn: 0.0471799	total: 1m 34s	remaining: 3m 9s
630:	learn: 0.0471318	total: 1m 34s	remaining: 3m 9s
631:	learn: 0.0471124	total: 1m 34s	remaining: 3m 9s
632:	learn: 0.0469369	total: 1m 34s	remaining: 3m 9s
633:	learn: 0.0468602	total: 1m 34s	remaining: 3m 9s
634:	learn: 0.0467860	total: 1m 34s	remaining: 3m 9s
635:	learn: 0.0467550	total: 1m 35s	remaining: 3m 8s
636:	learn: 0.0467276	total: 1m 35s	remaining: 3m 8s
637:	learn: 0.0466659	total: 1m 35s	remaining: 3m 8s
638:	learn: 0.0465937	total: 1m 35s	remaining: 3m 8s
639:	learn: 0.0465003	total: 1m 35s	remaining: 3m 8s
640:	learn: 0.0464740	total: 1m 35s	remaining: 3m 8s
641:	learn: 0.0464344	total: 1m 35s	remaining: 3m 7s
642:	learn: 0.0463731	total: 1m 36s	remaining: 3m 7s
643:	learn: 0.0463439	total: 1m 36s	remaini

...

1239:	learn: 0.0227268	total: 3m 7s	remaining: 1m 39s
1240:	learn: 0.0226689	total: 3m 7s	remaining: 1m 39s
1241:	learn: 0.0226564	total: 3m 8s	remaining: 1m 39s
1242:	learn: 0.0226507	total: 3m 8s	remaining: 1m 39s
1243:	learn: 0.0226315	total: 3m 8s	remaining: 1m 39s
1244:	learn: 0.0226153	total: 3m 8s	remaining: 1m 39s
1245:	learn: 0.0226016	total: 3m 8s	remaining: 1m 39s
1246:	learn: 0.0225934	total: 3m 8s	remaining: 1m 38s
1247:	learn: 0.0225672	total: 3m 9s	remaining: 1m 38s
1248:	learn: 0.0225445	total: 3m 9s	remaining: 1m 38s
1249:	learn: 0.0225405	total: 3m 9s	remaining: 1m 38s
1250:	learn: 0.0225334	total: 3m 9s	remaining: 1m 38s
1251:	learn: 0.0225224	total: 3m 9s	remaining: 1m 38s
1252:	learn: 0.0224960	total: 3m 9s	remaining: 1m 37s
1253:	learn: 0.0224723	total: 3m 9s	remaining: 1m 37s
1254:	learn: 0.0224538	total: 3m 10s	remaining: 1m 37s
1255:	learn: 0.0224465	total: 3m 10s	remaining: 1m 37s
1256:	learn: 0.0224017	total: 3m 10s	remaining: 1m 37s
1257:	learn: 0.0223988	to

1390:	learn: 0.0202412	total: 3m 29s	remaining: 1m 16s
1391:	learn: 0.0202308	total: 3m 30s	remaining: 1m 16s
1392:	learn: 0.0202129	total: 3m 30s	remaining: 1m 16s
1393:	learn: 0.0202031	total: 3m 30s	remaining: 1m 16s
1394:	learn: 0.0201788	total: 3m 30s	remaining: 1m 16s
1395:	learn: 0.0201732	total: 3m 30s	remaining: 1m 16s
1396:	learn: 0.0201679	total: 3m 30s	remaining: 1m 15s
1397:	learn: 0.0201502	total: 3m 31s	remaining: 1m 15s
1398:	learn: 0.0201150	total: 3m 31s	remaining: 1m 15s
1399:	learn: 0.0200885	total: 3m 31s	remaining: 1m 15s
1400:	learn: 0.0200767	total: 3m 31s	remaining: 1m 15s
1401:	learn: 0.0200566	total: 3m 31s	remaining: 1m 15s
1402:	learn: 0.0200501	total: 3m 31s	remaining: 1m 15s
1403:	learn: 0.0200312	total: 3m 31s	remaining: 1m 14s
1404:	learn: 0.0200244	total: 3m 32s	remaining: 1m 14s
1405:	learn: 0.0199990	total: 3m 32s	remaining: 1m 14s
1406:	learn: 0.0199764	total: 3m 32s	remaining: 1m 14s
1407:	learn: 0.0199575	total: 3m 32s	remaining: 1m 14s
1408:	lear

1543:	learn: 0.0179928	total: 3m 52s	remaining: 53.7s
1544:	learn: 0.0179776	total: 3m 52s	remaining: 53.5s
1545:	learn: 0.0179661	total: 3m 52s	remaining: 53.3s
1546:	learn: 0.0179403	total: 3m 53s	remaining: 53.2s
1547:	learn: 0.0179367	total: 3m 53s	remaining: 53s
1548:	learn: 0.0179203	total: 3m 53s	remaining: 52.9s
1549:	learn: 0.0179114	total: 3m 53s	remaining: 52.7s
1550:	learn: 0.0179045	total: 3m 53s	remaining: 52.6s
1551:	learn: 0.0178988	total: 3m 53s	remaining: 52.4s
1552:	learn: 0.0178846	total: 3m 53s	remaining: 52.3s
1553:	learn: 0.0178739	total: 3m 54s	remaining: 52.1s
1554:	learn: 0.0178636	total: 3m 54s	remaining: 51.9s
1555:	learn: 0.0178546	total: 3m 54s	remaining: 51.8s
1556:	learn: 0.0178473	total: 3m 54s	remaining: 51.6s
1557:	learn: 0.0178348	total: 3m 54s	remaining: 51.5s
1558:	learn: 0.0178239	total: 3m 54s	remaining: 51.3s
1559:	learn: 0.0178179	total: 3m 54s	remaining: 51.2s
1560:	learn: 0.0178165	total: 3m 54s	remaining: 51s
1561:	learn: 0.0178019	total: 3m

1697:	learn: 0.0162248	total: 4m 19s	remaining: 30.8s
1698:	learn: 0.0162177	total: 4m 19s	remaining: 30.7s
1699:	learn: 0.0161928	total: 4m 19s	remaining: 30.5s
1700:	learn: 0.0161870	total: 4m 19s	remaining: 30.4s
1701:	learn: 0.0161829	total: 4m 19s	remaining: 30.2s
1702:	learn: 0.0161795	total: 4m 20s	remaining: 30.1s
1703:	learn: 0.0161661	total: 4m 20s	remaining: 29.9s
1704:	learn: 0.0161548	total: 4m 20s	remaining: 29.8s
1705:	learn: 0.0161479	total: 4m 20s	remaining: 29.6s
1706:	learn: 0.0161365	total: 4m 20s	remaining: 29.5s
1707:	learn: 0.0161277	total: 4m 20s	remaining: 29.3s
1708:	learn: 0.0161218	total: 4m 21s	remaining: 29.2s
1709:	learn: 0.0161061	total: 4m 21s	remaining: 29s
1710:	learn: 0.0161013	total: 4m 21s	remaining: 28.9s
1711:	learn: 0.0160938	total: 4m 21s	remaining: 28.7s
1712:	learn: 0.0160844	total: 4m 21s	remaining: 28.6s
1713:	learn: 0.0160728	total: 4m 21s	remaining: 28.4s
1714:	learn: 0.0160666	total: 4m 21s	remaining: 28.3s
1715:	learn: 0.0160581	total: 

1851:	learn: 0.0149153	total: 4m 42s	remaining: 7.33s
1852:	learn: 0.0149100	total: 4m 43s	remaining: 7.18s
1853:	learn: 0.0148944	total: 4m 43s	remaining: 7.03s
1854:	learn: 0.0148879	total: 4m 43s	remaining: 6.87s
1855:	learn: 0.0148638	total: 4m 43s	remaining: 6.72s
1856:	learn: 0.0148589	total: 4m 43s	remaining: 6.57s
1857:	learn: 0.0148524	total: 4m 43s	remaining: 6.42s
1858:	learn: 0.0148390	total: 4m 43s	remaining: 6.26s
1859:	learn: 0.0148346	total: 4m 44s	remaining: 6.11s
1860:	learn: 0.0148294	total: 4m 44s	remaining: 5.96s
1861:	learn: 0.0148207	total: 4m 44s	remaining: 5.8s
1862:	learn: 0.0148147	total: 4m 44s	remaining: 5.65s
1863:	learn: 0.0148050	total: 4m 44s	remaining: 5.5s
1864:	learn: 0.0148027	total: 4m 44s	remaining: 5.35s
1865:	learn: 0.0147972	total: 4m 45s	remaining: 5.19s
1866:	learn: 0.0147938	total: 4m 45s	remaining: 5.04s
1867:	learn: 0.0147790	total: 4m 45s	remaining: 4.89s
1868:	learn: 0.0147729	total: 4m 45s	remaining: 4.74s
1869:	learn: 0.0147607	total: 

In [20]:
print(f'CatBoost train F1 Score {f1_score(y_train_labels, cat_cls.predict(X_train))}')
print(f'CatBoost train Accuracy {accuracy_score(y_train_labels, cat_cls.predict(X_train))}')
print(f'CatBoost test  F1 Score {f1_score(y_test_labels, cat_cls.predict(X_test))}')
print(f'CatBoost test  Accuracy {accuracy_score(y_test_labels, cat_cls.predict(X_test))}')

CatBoost train F1 Score 0.9988719684151156
CatBoost train Accuracy 0.9991598403696702
CatBoost test  F1 Score 0.8842471714534378
CatBoost test  Accuracy 0.9161940768746062


In [23]:
cat_cls.save_model("cb_88_91.pkl")

In [ ]:
import numpy as np
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt

X = X_train
y = y_train_labels

tsne = TSNE(n_components=2, random_state=42)

# Fit and transform data
X_tsne = tsne.fit_transform(X)

# Plot figures
plt.figure(figsize=(10, 8))
plt.scatter(X_tsne[y==0, 0], X_tsne[y==0, 1], color='blue', label='Negative')
plt.scatter(X_tsne[y==1, 0], X_tsne[y==1, 1], color='red', label='Positive')
plt.legend()
plt.show()


In [ ]:
from sklearn.ensemble import GradientBoostingClassifier
m = GradientBoostingClassifier()
m.fit(X_train, y_train_labels)

print(f'GradientBoostingClassifier F1 Score {f1_score(y_test_labels, m.predict(X_test))}')
print(f'GradientBoostingClassifier Accuracy {accuracy_score(y_test_labels, m.predict(X_test))}')

In [ ]:
from sklearn.ensemble import RandomForestClassifier
m = RandomForestClassifier()
m.fit(X_train, y_train_labels) 

print(f'RandomForestClassifier F1 Score {f1_score(y_test_labels, m.predict(X_test))}')
print(f'RandomForestClassifier Accuracy {accuracy_score(y_test_labels, m.predict(X_test))}')

In [ ]:
from sklearn.tree import DecisionTreeClassifier
m = DecisionTreeClassifier()
m.fit(X_train, y_train_labels) 

print(f'DecisionTreeClassifier F1 Score {f1_score(y_test_labels, m.predict(X_test))}')
print(f'DecisionTreeClassifier Accuracy {accuracy_score(y_test_labels, m.predict(X_test))}')

In [ ]:
from sklearn.svm import SVC
m = SVC(kernel='linear')
m.fit(X_train, y_train_labels) 

print(f'SVC F1 Score {f1_score(y_test_labels, m.predict(X_test))}')
print(f'SVC Accuracy {accuracy_score(y_test_labels, m.predict(X_test))}')

In [ ]:
import pickle

pickle.dump(m, open('svc_model_best', 'wb'))


In [ ]:
from matplotlib import pyplot as plt
colors = ["r", "b"]
for elem, ans in zip(X_train[:20], y_train_labels):
    plt.plot(elem, color=colors[ans])

In [ ]:
plt.plot(np.arange(len((m.coef_[0]))), m.coef_[0])

In [ ]:
from sklearn.linear_model import LogisticRegression
m = LogisticRegression(max_iter=10000)
m.fit(X_train, y_train_labels) 

print(f'LogisticRegression F1 Score {f1_score(y_test_labels, m.predict(X_test))}')
print(f'LogisticRegression Accuracy {accuracy_score(y_test_labels, m.predict(X_test))}')

In [ ]:
import pickle

pickle.dump(m, open('logistic_model_best', 'wb'))
